### Requirements

- Installed git. More on how to use and install git can be found [here][git]. 
- A zip of the certificate. Particularly, you'll need the crt and key files.
- A labkey access configuration file. A sample for [linux][linuxConfig] or [Windows][windowsConfig]. The file paths point to locations of extracted files from certificate zip on your disk.

[git]: https://git-scm.com/
[linuxConfig]: https://git0.fmf.uni-lj.si/studen/labkeyInterface/src/master/network-config-sample.json
[windowsConfig]: https://git0.fmf.uni-lj.si/studen/labkeyInterface/src/master/network-config-sample.json

In [2]:
#load required libraries
import sys
import os
import SimpleITK
import numpy
import matplotlib.pyplot
import chardet
import json

#you should get nixSuite via git clone https://git0.fmf.uni-lj.si/studen/nixSuite.git
#if you don't put it to $HOME/software/src/, you should update the path
nixSuite=os.path.join(os.path.expanduser('~'),'software','src','nixSuite')
sys.path.append(os.path.join(nixSuite,'wrapper'))
import nixWrapper
nixWrapper.loadLibrary('labkeyInterface')
import labkeyInterface
import labkeyDatabaseBrowser
import labkeyFileBrowser



remoteSourcesURL https://git0.fmf.uni-lj.si/studen/nixSuite/raw/master/remoteResources/resources.json
{'labkeyInterface': {'url': 'https://git0.fmf.uni-lj.si/studen/labkeyInterface/archive/master.zip', 'branch': 'master', 'modules': []}, 'irAEMM': {'url': 'https://git0.fmf.uni-lj.si/studen/iraemm/archive/master.zip', 'branch': 'master', 'modules': ['iraemmBrowser']}, 'SlicerLabkeyExtension': {'url': 'https://git0.fmf.uni-lj.si/studen/SlicerLabkeyExtension/archive/SlicerExtensionIndex.zip', 'branch': 'SlicerExtensionIndex', 'modules': ['labkeyBrowser']}, 'limfomiPET': {'url': 'https://git0.fmf.uni-lj.si/studen/limfomiPET/archive/master.zip', 'branch': 'master', 'modules': ['imageBrowser']}, 'parseConfig': {'url': 'https://git0.fmf.uni-lj.si/studen/parseConfig/archive/master.zip', 'branch': 'master', 'modules': []}, 'orthancInterface': {'url': 'https://git0.fmf.uni-lj.si/studen/orthancInterface/archive/master.zip', 'branch': 'master', 'modules': []}}


In [3]:
#check connectivity. This checks the configuration in $HOME/.labkey/network.json, 
#where paths to certificates are stored
net=labkeyInterface.labkeyInterface()
fconfig=os.path.join(os.path.expanduser('~'),'.labkey','labkey-klimt.json')
#fconfig=os.path.join(os.path.expanduser('~'),'.labkey','merlin.json')
net.init(fconfig)
#this reports the certificate used
try:
    print('Using: {}'.format(net.connectionConfig['SSL']['user']))
except KeyError:
    pass
#This gets a deafult CSRF code; It should report user name plus a long string of random hex numbers
net.getCSRF()

User: andrej studen CSRF: 71c3c9c047d735e94769566bc7a30b05


'71c3c9c047d735e94769566bc7a30b05'

In [ ]:
db=labkeyDatabaseBrowser.labkeyDB(net)
fb=labkeyFileBrowser.labkeyFileBrowser(net)
#select a project
project='dinamic_spect/Patients'
project='hypoAfrica/Study'
dataset='Segmentation'
schema='lists'
query='crfEntry'
#idFilter={'variable':'ParticipantId','value':'VUB_PA3','oper':'eq'}
#aliasFilter={'variable':'aliasID','value':'3OBR','oper':'eq'}
#empty filter
qFilter=[]
#qFilter can be a list of filters used in conjugation (logical AND)
#qFilter=[aliasFilter]
ds=db.selectRows(project,schema,query,qFilter)
rows=ds['rows']
alias={'1063':'1014','1093':'1015','1094':'1016','1095':'1017','1096':'1018',
       '1097':'1019','1098':'1020','1099':'1021','1100':'1022',
       '1106':'1023','1114':'1024','1122':'1025',
       '1124':'1026','1125':'1027',
       '1126':'1028','1127':'1029'}
for row in rows:
    #row as a dictionary
    #print(row)
    #update row
    #depending on field type adjust newValue
    field='crfMonitor'
    uid=row[field]
    if uid==None:
        continue
    print(uid)
    if int(uid)>1030:
        row[field]=int(alias['{}'.format(uid)])
    #row['visitId']='OBR'
    #print the new row
    print(row)
    #change the value of the field in database 
    #if field is not in database, it will NOT be added and no changes will occur
    db.modifyRows('update',project,schema,query,[row])    
        

In [36]:
net1=labkeyInterface.labkeyInterface()
fconfig1=os.path.join(os.path.expanduser('~'),'.labkey','labkey-public.json')
net1.init(fconfig1)
net1.getCSRF()

net2=labkeyInterface.labkeyInterface()
fconfig2=os.path.join(os.path.expanduser('~'),'.labkey','labkey-klimt.json')
net2.init(fconfig2)
net2.getCSRF()

db1=labkeyDatabaseBrowser.labkeyDB(net1)
#select a project
project1='hypoAfrica/Study'
schema1='study'
query1='consentList'

db2=labkeyDatabaseBrowser.labkeyDB(net2)
#select a project
project2='hypoAfrica/Study'
schema2='study'
query2=query1
#idFilter={'variable':'ParticipantId','value':'VUB_PA3','oper':'eq'}
#aliasFilter={'variable':'aliasID','value':'3OBR','oper':'eq'}
#empty filter
qFilter=[]
#qFilter can be a list of filters used in conjugation (logical AND)
#qFilter=[aliasFilter]
ds=db1.selectRows(project1,schema1,query1,qFilter)
rows=ds['rows']
for row in rows:
    #row as a dictionary
    print(row)
    #update row
    #depending on field type adjust newValue
    #change the value of the field in database 
    #if field is not in database, it will NOT be added and no changes will occur
    print(db2.modifyRows('insert',project2,schema2,query2,[row]))
        

User: andrej studen CSRF: 8d5073a5a0f98622de543f64ab8319cc
User: andrej studen CSRF: 826b45d185e85d1780e89b3aac079a39
{'ParticipantId': 'JOHN003', 'followUpDuration': 1, 'lsid': 'urn:lsid:labkey.com:Study.Data-61:5011.JOHN003.243390879.0000', '_labkeyurl_followUpDuration': '/labkey/hypoAfrica/Study/list-details.view?listId=141&pk=1', '_labkeyurl_ParticipantId': '/labkey/hypoAfrica/Study/study-participant.view?participantId=JOHN003', 'crfRef': '1649243390879', 'submissionDate': '2022/04/06 14:00:00', 'SequenceNum': 243390879.0}
User: andrej studen CSRF: b0d3f22a0a97552c9877c12e0c15c803
b'{\n  "rowsAffected" : 1,\n  "queryName" : "consentList",\n  "schemaName" : "study",\n  "containerPath" : "/hypoAfrica/Study",\n  "rows" : [ {\n    "date" : null,\n    "followUpDuration" : 1,\n    "ParticipantVisit" : "JOHN003|243390879.0000",\n    "dsrowid" : 1,\n    "CreatedBy" : 1003,\n    "Modified" : "2022-11-29 16:16:05.479",\n    "DataSets" : "JOHN003",\n    "QCState" : null,\n    "submissionDate"